In [4]:
import sys
import time
import warnings
from pathlib import Path

import pandas as pd
import numpy as np
import optuna
import mlflow

# -------------------------------------------------
# Project path (add ONCE)
# -------------------------------------------------
sys.path.insert(
    0, r"C:\Users\user.IBRAHIM-IK-SZHE\hyperopt-llm-project\src"
)


# -------------------------------------------------
# Ignore warnings safely
# -------------------------------------------------
warnings.filterwarnings("ignore")

# -------------------------------------------------
# Project imports
# -------------------------------------------------
from data.data_preprocessing import DataPreprocessing
from models.model import BiLSTMForecast
from pipelines.forecasting_pipeline import ForecastingPipeline
from tuning.bo_tuning import BayesianOptimization
from meta_HPO.meta_knowledge_building import MetaKnowledgeBuilder
from tuning.meta_llm_tuning import LLMTuning
from models.plot_results import ResultsPlotter


In [ ]:
'''
# Data preprocesing of the Jenna Weather Dataset
RAW_TRAIN_PATH= "C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/data/raw_data/train.csv"
RAW_TEST_PATH = "C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/data/raw_data/eval.csv"
train_df = pd.read_csv(RAW_TRAIN_PATH,parse_dates=True, index_col="Date Time")
test_df = pd.read_csv(RAW_TEST_PATH,parse_dates=True,index_col ="Date Time")
#------Clean Raw Train Data-------------------
cl_train  = CleanData(train_df)
clean_train = cl_train.clean(train_df)
clean_train = cl_train.interpolate(clean_train)
clean_train = cl_train.feature_selection("clean_train",clean_train)
#------Clea
# n Raw Test Data-------------------
cl_test  = CleanData(test_df)
clean_test = cl_test.clean(test_df)
clean_test  = cl_test.interpolate(clean_test)
clean_test= cl_test.feature_selection("clean_test",clean_test)'''


'\n# Data preprocesing\nRAW_TRAIN_PATH= "C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/data/raw_data/train.csv"\nRAW_TEST_PATH = "C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/data/raw_data/eval.csv"\ntrain_df = pd.read_csv(RAW_TRAIN_PATH,parse_dates=True, index_col="Date Time")\ntest_df = pd.read_csv(RAW_TEST_PATH,parse_dates=True,index_col ="Date Time")\n#------Clean Raw Train Data-------------------\ncl_train  = CleanData(train_df)\nclean_train = cl_train.clean(train_df)\nclean_train = cl_train.interpolate(clean_train)\nclean_train = cl_train.feature_selection("clean_train",clean_train)\n#------Clea\n# n Raw Test Data-------------------\ncl_test  = CleanData(test_df)\nclean_test = cl_test.clean(test_df)\nclean_test  = cl_test.interpolate(clean_test)\nclean_test= cl_test.feature_selection("clean_test",clean_test)'

In [5]:
#-------------------Loading Data-------------------
MLFLOW_PATH = "file:///C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/mlruns"
TARGET_COLS =['T (degC)', 'rh (%)', 'p (mbar)', 'wv (m/s)']
clean_train = pd.read_csv('C:/Users/user.IBRAHIM-IK-SZHE/Meta_LLM_HPO/hyperopt-llm-project/data/clean_data/clean_train.csv',
    parse_dates=["datetime"],
    index_col="datetime"
    )
clean_test = pd.read_csv('C:/Users/user.IBRAHIM-IK-SZHE/Meta_LLM_HPO/hyperopt-llm-project/data/clean_data/clean_test.csv', 
    parse_dates=["datetime"],
    index_col="datetime"
    )

# 1 . Base Forecasting Model

In [6]:

# Create Base Forecasting Model 
#--------------------------
 #Define Forecasting Pipeline
#--------------------------

TARGET_COLS =['T (degC)', 'rh (%)', 'p (mbar)', 'wv (m/s)']
PARAMS = {
    "hidden_size": 5,
    "num_layers": 6,
    "dropout": 0.1,
    "batch_size": 128,
    "epochs": 10,
    "lag": 3,
    "kernel_size": 5,
    "optimizer": "adam",
    "lr": 1e-3,
}
name_model = "Bi-LSTM"
experiment_name ="base_forecasting_Model"
MLFLOW_PATH = "file:///C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/mlruns"

# define ForecastingPipeline
pipeline = ForecastingPipeline(
    clean_train=clean_train,
    clean_test=clean_test,
    target_cols=TARGET_COLS,
    experiment_name=experiment_name,
   mlflow_uri=MLFLOW_PATH
)
results = pipeline.run(name_model,PARAMS,run_suffix=experiment_name)

2026/01/29 07:00:59 INFO mlflow.tracking.fluent: Experiment with name 'base_forecasting_Model' does not exist. Creating a new experiment.


Epoch [1/10] Loss: 0.190460 | RMSE: 0.437514
Epoch [2/10] Loss: 0.040303 | RMSE: 0.200631
Epoch [3/10] Loss: 0.039152 | RMSE: 0.197879
Epoch [4/10] Loss: 0.033475 | RMSE: 0.182951
Epoch [5/10] Loss: 0.029674 | RMSE: 0.172157
Epoch [6/10] Loss: 0.027079 | RMSE: 0.164440
Epoch [7/10] Loss: 0.025303 | RMSE: 0.158843
Epoch [8/10] Loss: 0.024268 | RMSE: 0.155627
Epoch [9/10] Loss: 0.023543 | RMSE: 0.153260
Epoch [10/10] Loss: 0.023079 | RMSE: 0.151808
Test RMSE: 5.9133 | SMAPE: 28.40%


# 2 . Bayesian Optimization Forecasting Models 

In [11]:

#***********************main Byesian Optimization***************************

bayesian_exp_name = "Bayesian_Optimization"
bo_model =  BayesianOptimization(clean_train,clean_test,TARGET_COLS,MLFLOW_PATH)
bo_opt_time = bo_model.run_bo(6)

[I 2026-01-29 07:30:12,182] A new study created in memory with name: no-name-0abef84b-fc12-4ca8-a856-ea75685455f0


Epoch [1/17] Loss: 0.096566 | RMSE: 0.310898
Epoch [2/17] Loss: 0.031272 | RMSE: 0.176688
Epoch [3/17] Loss: 0.024818 | RMSE: 0.157471
Epoch [4/17] Loss: 0.016601 | RMSE: 0.128836
Epoch [5/17] Loss: 0.011267 | RMSE: 0.106148
Epoch [6/17] Loss: 0.007556 | RMSE: 0.086915
Epoch [7/17] Loss: 0.005577 | RMSE: 0.074656
Epoch [8/17] Loss: 0.003863 | RMSE: 0.062130
Epoch [9/17] Loss: 0.002994 | RMSE: 0.054681
Epoch [10/17] Loss: 0.002572 | RMSE: 0.050674
Epoch [11/17] Loss: 0.002256 | RMSE: 0.047461
Epoch [12/17] Loss: 0.002028 | RMSE: 0.044991
Epoch [13/17] Loss: 0.001853 | RMSE: 0.042999
Epoch [14/17] Loss: 0.001731 | RMSE: 0.041554
Epoch [15/17] Loss: 0.001677 | RMSE: 0.040899
Epoch [16/17] Loss: 0.001682 | RMSE: 0.040956
Epoch [17/17] Loss: 0.001600 | RMSE: 0.039942
Test RMSE: 1.6823 | SMAPE: 11.22%


[I 2026-01-29 07:44:26,399] Trial 0 finished with value: 1.6823282317117243 and parameters: {'num_layers': 2, 'dropout': 0.00984134521029112, 'lag': 61, 'hidden_size': 127, 'lr': 0.00013247461160376117, 'batch_size': 128, 'epochs': 17, 'optimizer': 'adam'}. Best is trial 0 with value: 1.6823282317117243.


Epoch [1/6] Loss: 0.051913 | RMSE: 0.227862
Epoch [2/6] Loss: 0.021413 | RMSE: 0.146358
Epoch [3/6] Loss: 0.014524 | RMSE: 0.120535
Epoch [4/6] Loss: 0.011093 | RMSE: 0.105336
Epoch [5/6] Loss: 0.009450 | RMSE: 0.097226
Epoch [6/6] Loss: 0.006142 | RMSE: 0.078376
Test RMSE: 2.8625 | SMAPE: 17.41%


[I 2026-01-29 07:47:11,791] Trial 1 finished with value: 2.8625347884076193 and parameters: {'num_layers': 3, 'dropout': 0.2289182709271414, 'lag': 33, 'hidden_size': 88, 'lr': 0.00022703193026767508, 'batch_size': 64, 'epochs': 6, 'optimizer': 'adam'}. Best is trial 0 with value: 1.6823282317117243.


...

Epoch [1/19] Loss: 0.055317 | RMSE: 0.235240
Epoch [2/19] Loss: 0.027397 | RMSE: 0.165557
Epoch [3/19] Loss: 0.019472 | RMSE: 0.139560
Epoch [4/19] Loss: 0.013540 | RMSE: 0.116372
Epoch [5/19] Loss: 0.011686 | RMSE: 0.108105
Epoch [6/19] Loss: 0.010119 | RMSE: 0.100594
Epoch [7/19] Loss: 0.006891 | RMSE: 0.082999
Epoch [8/19] Loss: 0.005564 | RMSE: 0.074563
Epoch [9/19] Loss: 0.003255 | RMSE: 0.057026
Epoch [10/19] Loss: 0.002423 | RMSE: 0.049191
Epoch [11/19] Loss: 0.002021 | RMSE: 0.044922
Epoch [12/19] Loss: 0.001763 | RMSE: 0.041948
Epoch [13/19] Loss: 0.001611 | RMSE: 0.040104
Epoch [14/19] Loss: 0.001584 | RMSE: 0.039762
Epoch [15/19] Loss: 0.001551 | RMSE: 0.039352
Epoch [16/19] Loss: 0.002018 | RMSE: 0.044847
Epoch [17/19] Loss: 0.002871 | RMSE: 0.053566
Epoch [18/19] Loss: 0.002902 | RMSE: 0.053793
Epoch [19/19] Loss: 0.002401 | RMSE: 0.048971
Test RMSE: 2.1764 | SMAPE: 11.39%


[I 2026-01-29 08:20:00,133] Trial 4 finished with value: 2.1763666815896063 and parameters: {'num_layers': 3, 'dropout': 0.3303840840917214, 'lag': 42, 'hidden_size': 107, 'lr': 0.0008095552921799354, 'batch_size': 128, 'epochs': 19, 'optimizer': 'adamw'}. Best is trial 0 with value: 1.6823282317117243.


Epoch [1/15] Loss: 0.021197 | RMSE: 0.145597
Epoch [2/15] Loss: 0.008435 | RMSE: 0.091788
Epoch [3/15] Loss: 0.004582 | RMSE: 0.067588
Epoch [4/15] Loss: 0.003779 | RMSE: 0.061353
Epoch [5/15] Loss: 0.003363 | RMSE: 0.057872
Epoch [6/15] Loss: 0.003035 | RMSE: 0.054961
Epoch [7/15] Loss: 0.002600 | RMSE: 0.050840
Epoch [8/15] Loss: 0.002170 | RMSE: 0.046409
Epoch [9/15] Loss: 0.001717 | RMSE: 0.041231
Epoch [10/15] Loss: 0.001449 | RMSE: 0.037834
Epoch [11/15] Loss: 0.001109 | RMSE: 0.033031
Epoch [12/15] Loss: 0.001095 | RMSE: 0.032827
Epoch [13/15] Loss: 0.001040 | RMSE: 0.031969
Epoch [14/15] Loss: 0.000995 | RMSE: 0.031284
Epoch [15/15] Loss: 0.000969 | RMSE: 0.030852
Test RMSE: 4.7449 | SMAPE: 11.26%


[I 2026-01-29 08:29:04,238] Trial 5 finished with value: inf and parameters: {'num_layers': 2, 'dropout': 0.040134822516104285, 'lag': 39, 'hidden_size': 121, 'lr': 0.004348157721686479, 'batch_size': 32, 'epochs': 15, 'optimizer': 'adamax'}. Best is trial 0 with value: 1.6823282317117243.


Trial 5 failed: 
Optimization took 3532.06 seconds


# 3. LLM-AutoOpt Framework

In [ ]:
#-------------------Extract and create meta-Knowledge--------------------------

builder = MetaKnowledgeBuilder(clean_train,"Bayesian_Optimization",TARGET_COLS)
builder.create_meta_trials(3)
builder.meta_features_creation()

{'dataset_regime': {'temporal_dependence': 'strong',
  'stationarity': 'mostly stationary',
  'trend': 'moderate',
  'seasonality': 'strong',
  'volatility': 'moderate',
  'noise_level': 'low'},
 'aggregated_meta': {'temporal_dependence_mean_acf1': 0.9842552224938796,
  'stationarity_ratio': 1.0,
  'avg_trend_strength': None,
  'avg_seasonality_strength': None,
  'avg_volatility_cv': 0.5201976930677733,
  'avg_nonlinearity_proxy': 0.7567171615967565,
  'avg_outlier_ratio': 0.011233859397417504},
 'raw_meta_features': {'T (degC)': {'count': 17425,
   'mean': 6.851520229555236,
   'std': 7.420269427945772,
   'coef_of_variation': 1.083010657392083,
   'min': -9.71,
   '25%': 0.7,
   '50%_median': 6.49,
   '75%': 12.3,
   'max': 28.57,
   'range': 38.28,
   'iqr': 11.600000000000001,
   'skewness': 0.2873137278815108,
   'kurtosis': -0.6140866854268237,
   'acf_lag_1': 0.9978089513413274,
   'acf_lag_3': 0.9920876624074284,
   'acf_lag_6': 0.98129129760696,
   'acf_lag_12': 0.952085295992

In [9]:

llm_name ="qwen2.5:3b" # it can be llm_name ="llama3:8b",llm_name =  "deepseek-r1:7b"
name_model = "Bi-LSTM"
experiment_name =f"LLM-AutoOpt_{llm_name}"

model_description = """
Bidirectional LSTM for multivariate forecasting:
- Input: multivariate sequence
- hidden_size: LSTM units
- num_layers: stacked layers
- dropout applied between layers
"""

meta_trials_data = "C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/data/meta_data/run_data.json"
meta_features_data = "C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/data/meta_data/meta_features.json"
llm_opt =  LLMTuning(name_model,experiment_name,clean_train,clean_test,TARGET_COLS,MLFLOW_PATH,llm_name,model_description,0.3)
llm_opt.run_llm_autoopt(4,meta_trials_data,meta_features_data)



2026/01/29 07:21:27 INFO mlflow.tracking.fluent: Experiment with name 'LLM-AutoOpt_qwen2.5:3b' does not exist. Creating a new experiment.



===== HPO Trial 1 =====
Suggested JSON: {
  "suggested_params": {
    "lag": 24,
    "hidden_size": 64,
    "num_layers": 1,
    "dropout": 0.15,
    "lr": 0.001,
    "batch_size": 32,
    "epochs": 40,
    "optimizer": "adam"
  },
  "meta_feature_reasoning": "The dataset has a lag of [12, 16, 24, 32] and the chosen lag is within this range. The hidden size of 64 balances model capacity with computational efficiency.",
  "non_repetition_check": "True",
  "expected_improvement": "The combination of increased dropout (0.15) and higher learning rate (0.001) are expected to reduce overfitting while still allowing the model to learn from the data."
}
Reasoning: The dataset has a lag of [12, 16, 24, 32] and the chosen lag is within this range. The hidden size of 64 balances model capacity with computational efficiency.
Epoch [1/40] Loss: 0.026265 | RMSE: 0.162081
Epoch [2/40] Loss: 0.006265 | RMSE: 0.079151
Epoch [3/40] Loss: 0.001961 | RMSE: 0.044266
Epoch [4/40] Loss: 0.001408 | RMSE: 0.0

In [12]:

#-------------------Ploting Results-------------------


save_dir = "C:/Users/user.IBRAHIM-IK-SZHE/hyperopt-llm-project/results/plots"
results_plots = ResultsPlotter(
    test_df=clean_test,
    rmse_threshold=6,
    mlflow_uri=MLFLOW_PATH
)

results_plots.plot_filtered_results(save_dir)

[670898797440576509] 'LLM-AutoOpt_qwen2.5:3b'
[531732418893150080] 'Bayesian_Optimization'
[290334297095323472] 'base_forecasting_Model'


{'results': [{'true': array([[ 1.14000030e+00,  9.10000000e+01,  9.85940001e+02,
            3.17000013e+00],
          [ 1.05999980e+00,  9.17000011e+01,  9.86000000e+02,
            3.50999993e+00],
          [ 9.80000385e-01,  9.24999980e+01,  9.86030000e+02,
            3.16000012e+00],
          ...,
          [ 1.22600004e+01,  9.05999994e+01,  9.91869999e+02,
            2.62000013e+00],
          [-8.03000000e+00,  9.20000015e+01,  9.97720000e+02,
            4.89999999e-01],
          [-7.91999999e+00,  9.18000012e+01,  9.97740001e+02,
            5.40000014e-01]]),
   'preds': array([[ 1.85797693e+00,  9.05041176e+01,  9.85586265e+02,
            3.61937725e+00],
          [ 1.62466359e+00,  9.14891206e+01,  9.85662540e+02,
            2.91034290e+00],
          [ 1.55561895e+00,  9.22436562e+01,  9.85735927e+02,
            3.14973224e+00],
          ...,
          [ 1.21364079e+01,  9.20194289e+01,  9.91544043e+02,
            2.36853536e+00],
          [ 1.21834349e+01,  9